In [1]:
%%capture
# Instalar la biblioteca pytube
!pip install pytube
!apt update && apt install -y handbrake

from pytube import YouTube

# URL del video de YouTube
url = 'https://www.youtube.com/watch?v=MCYFlhCyHHw'

# Crear un objeto YouTube
yt = YouTube(url)

# Seleccionar el stream con resolución de 720p
video = yt.streams.filter(progressive=True, file_extension='mp4', res="720p").first()

# Nombre del archivo de salida
output_filename = 'CalleAutosMotos.mp4'

# Descargar el video con el nombre especificado
video.download(filename=output_filename)

print("Descarga completada.")

In [2]:
%pip install ultralytics
# Librería mediapy para mostrar videos
%pip install -q mediapy
import ultralytics
ultralytics.checks()

Ultralytics YOLOv8.2.2 🚀 Python-3.10.12 torch-2.2.1+cu121 CPU (Intel Xeon 2.20GHz)
Setup complete ✅ (2 CPUs, 12.7 GB RAM, 28.9/107.7 GB disk)


In [ ]:
# Importamos las librerías a utilizar
# import cv2
# from ultralytics import YOLO
# from IPython.display import Image

# # Load the pre-trained YOLOv8 model
# model = YOLO('yolov8n')  # This will automatically download the model weights

# # Perform inference
# source_img = cv2.imread('https://ultralytics.com/images/bus.jpg')
# results = model(source_img)

# # Visualize the results on the frame
# annotated_frame = results[0].plot()

# # Guardamos el resultado en JPG
# cv2.imwrite('bus_results.jpg', annotated_frame)

# # Mostramos el resultado en Colab
# Image('bus_results.jpg')

In [3]:
! [ ! -f highway_600.mp4 ] &&  wget /content/CalleAutosMotos.mp4
!yolo predict model=yolov8n.pt source='CalleAutosMotos.mp4' save=True project=highway_yolov8

/content/CalleAutosMotos.mp4: Scheme missing.
100% 6.23M/6.23M [00:00<00:00, 82.9MB/s]
Ultralytics YOLOv8.2.2 🚀 Python-3.10.12 torch-2.2.1+cu121 CPU (Intel Xeon 2.20GHz)
YOLOv8n summary (fused): 168 layers, 3151904 parameters, 0 gradients, 8.7 GFLOPs

video 1/1 (frame 1/1537) /content/CalleAutosMotos.mp4: 384x640 25 cars, 3 buss, 5 trucks, 273.5ms
video 1/1 (frame 2/1537) /content/CalleAutosMotos.mp4: 384x640 24 cars, 4 buss, 5 trucks, 166.2ms
video 1/1 (frame 3/1537) /content/CalleAutosMotos.mp4: 384x640 26 cars, 4 buss, 3 trucks, 143.2ms
video 1/1 (frame 4/1537) /content/CalleAutosMotos.mp4: 384x640 27 cars, 4 buss, 4 trucks, 1 traffic light, 142.0ms
video 1/1 (frame 5/1537) /content/CalleAutosMotos.mp4: 384x640 28 cars, 3 buss, 4 trucks, 146.4ms
video 1/1 (frame 6/1537) /content/CalleAutosMotos.mp4: 384x640 29 cars, 2 buss, 4 trucks, 135.0ms
video 1/1 (frame 7/1537) /content/CalleAutosMotos.mp4: 384x640 27 cars, 3 buss, 4 trucks, 142.8ms
video 1/1 (frame 8/1537) /content/CalleAutosM

In [7]:
import mediapy as media  # Importar la biblioteca mediapy para manejo de medios
import cv2  # Importar OpenCV para el procesamiento de imágenes y videos
import numpy as np
from ultralytics import YOLO

# Load the pre-trained YOLOv8 model
model = YOLO('yolov8n')  # This will automatically download the model weights

# Función para detectar objetos en una imagen:
def detect_objects(new_image, prev_image, **kwargs):
    # Convertir la imagen a float32
    results = model(new_image)

    # Clases de interés para graficar
    classes = kwargs.get('classes', ['person'])

    # Iteramos sobre los boung boxes obtenidos
    for box in results[0].boxes:
        # Extrayendo los datos del tensor
        x1, y1, x2, y2, confidence, cls = box.data[0]

        # Obteniendo el nombre de la clase
        class_name = model.names[int(cls)]

        # Parámetros opcionales del bounding box
        color = kwargs.get('color', (0, 255, 0))
        thickness = kwargs.get('thickness', 2)

        if class_name in classes:
            # Dibujar el rectángulo
            cv2.rectangle(new_image, (int(x1), int(y1)), (int(x2), int(y2)), color, thickness)

            # Agregar el texto de la confianza
            confidence_text = f"{class_name}: {confidence:.2f}"
            cv2.putText(new_image, confidence_text, (int(x1), int(y1)-10), cv2.FONT_HERSHEY_SIMPLEX, 0.5, color, 2)

    return new_image

# Función para procesar un video:
def video_processor(filename_in, filename_out, process_func, max_time=10, **kwargs):
    # Abrir el video de entrada para lectura
    with media.VideoReader(filename_in) as r:
        # Crear un archivo de video de salida
        with media.VideoWriter(filename_out, shape=r.shape, fps=r.fps, bps=r.bps) as w:
            count = 0  # Inicializar contador de fotogramas
            prev_image = None  # Inicializar la imagen previa

            # Iterar sobre cada imagen (fotograma) del video
            for image in r:
                new_image = media.to_uint8(image)  # Convertir la imagen a formato flotante

                # Comprobar si es la primera imagen
                if prev_image is None:
                    prev_image = new_image.copy()

                # Procesar la imagen utilizando la función dada
                processed_image = process_func(new_image, prev_image, **kwargs)

                # Añadir la imagen procesada al video de salida
                w.add_image(processed_image)

                # Actualizar la imagen previa
                prev_image = new_image.copy()

                # Incrementar el contador de fotogramas
                count += 1

                # Detener el proceso si se alcanza el tiempo máximo
                if count >= max_time * r.fps:
                    break

# Nombres de los archivos de video de entrada y salida
filename_in = 'CalleAutosMotos.mp4'
filename_out = 'SoloMotos.mp4'
parameters = dict(classes=['person'])    # ['bus', 'car', 'truck']

# Llamar a la función para procesar el video
video_processor(filename_in, filename_out, detect_objects, 20, **parameters)

# Mostrar el video resultante
media.show_video(media.read_video(filename_out), fps=30)


0: 384x640 25 cars, 2 buss, 4 trucks, 247.2ms
Speed: 5.7ms preprocess, 247.2ms inference, 2.1ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 25 cars, 2 buss, 4 trucks, 258.1ms
Speed: 2.7ms preprocess, 258.1ms inference, 1.8ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 25 cars, 3 buss, 2 trucks, 224.6ms
Speed: 3.8ms preprocess, 224.6ms inference, 1.9ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 26 cars, 2 buss, 5 trucks, 1 traffic light, 217.6ms
Speed: 2.6ms preprocess, 217.6ms inference, 1.8ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 23 cars, 3 buss, 4 trucks, 231.5ms
Speed: 3.1ms preprocess, 231.5ms inference, 1.7ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 25 cars, 2 buss, 4 trucks, 226.1ms
Speed: 4.5ms preprocess, 226.1ms inference, 1.8ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 24 cars, 2 buss, 3 trucks, 210.4ms
Speed: 2.6ms preprocess, 210.4ms inference, 1.6ms postprocess per 

This browser does not support the video tag.
